# Importing requirements

In [ ]:
import pandas as pd

df = pd.read_csv('df_Req_Final.csv')

print(df.head())
print(df.shape)

Mounted at /gdrive
   Unnamed: 0                                               Text  Estimate  \
0       23009  add ca against object literals in function inv...         1   
1       23013  update branding for appcelerator plugin to app...         1   
2       23003  create new json schema for sdk team{html}<div>...         1   
3       23012  create project references property page{html}<...         1   
4       23007  new desktop project wizard{html}<div><p>deskto...         1   

                                             Cleaned  
0  add ca against object literals in function inv...  
1  update branding for appcelerator plugin to app...  
2  create new json schema for sdk team create jso...  
3  create project references property page create...  
4  new desktop project wizard desktop need to con...  
(23313, 4)


# Generating embeddings for tokens with less than 2000 tokens

Removing requirements bigger than 2000 tokens

In [ ]:
%pip install transformers openai --quiet

In [ ]:
from transformers import GPT2TokenizerFast
tokenizer = GPT2TokenizerFast.from_pretrained("gpt2")

# remove requirements that are too long
df['n_tokens'] = df['Cleaned'].apply(lambda x: len(tokenizer.encode(x)))
req_before = len(df['Cleaned'])
tokens_before = sum(df['n_tokens'])
df = df[df.n_tokens<2000]
req_after = len(df['Cleaned'])
tokens_after = sum(df['n_tokens'])

print('starting requirements number',req_before)
print('requirements number at end', req_after)

print('starting nof tokens',tokens_before)
print('ending nof tokens', tokens_after)

     |████████████████████████████████| 4.9 MB 9.0 MB/s 
     |████████████████████████████████| 43 kB 1.9 MB/s 
  Installing build dependencies ... done
  Getting requirements to build wheel ... done
    Preparing wheel metadata ... done
     |████████████████████████████████| 120 kB 53.5 MB/s 
     |████████████████████████████████| 6.6 MB 20.6 MB/s 
     |████████████████████████████████| 163 kB 47.5 MB/s 


Downloading:   0%|          | 0.00/1.04M [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/456k [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/1.36M [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/665 [00:00<?, ?B/s]

Token indices sequence length is longer than the specified maximum sequence length for this model (2493 > 1024). Running this sequence through the model will result in indexing errors


num requisitos antes 23313
num requisitos depois 23123
tokens antes 3011162
tokens depois 2473212


Estimating price of embeddings generation

In [ ]:
print('number of tokens: ',tokens_after)
pricing_1k_tokens_babbage = 0.0050
estimated_price = tokens_after * pricing_1k_tokens_babbage / 1000
print('estimated price: $',estimated_price)
# $ 0.0050/1K

numero de tokens:  2473212
preço estimado: $ 12.36606


***Gerando os embeddings***

In [ ]:
#getting timedate to name the file
from datetime import datetime
import time

now = datetime.now()
current_time = now.strftime("%d-%m-%y_%Hh%Mmin")

import openai
# from openai.embeddings_utils import get_embedding
# openai.api_key = '?'
times = []
def get_embedding(text, model="text-similarity-babbage-001"):
  start = time.time()

  text = text.replace("\n", " ")
  embedding = openai.Embedding.create(input = [text], model=model)['data'][0]['embedding']

  if((len(times)%100)==0): # prints every hundredth of requests
    print(len(times))
  
  # controls the elapsed time (due to max API call frequency)
  elapsed = time.time() - start
  times.append(elapsed)
  if(elapsed < 0.02):
    time.sleep(0.02-elapsed)
  return embedding

df['babbage_similarity'] = df['Cleaned'].apply(lambda x: get_embedding(x, model='text-similarity-babbage-001'))

Copying embeddings to a new dataframe and saving it on a pickle file

In [ ]:
df2 = df['babbage_similarity'].copy()
df2.to_pickle('df_embeddings_pickle_2.pkl', index=False)

# generating embeddings for requirements with +2000 tokens

In [ ]:
import pandas as pd

df = pd.read_pickle('df_Final_Join_Embeddings.pkl')


In [ ]:
# Estimating costs:

total_reqs = 23313
reqs_with_more_than_2000_tokens = 23123
tokens_number = 2000 * (total_reqs-reqs_with_more_than_2000_tokens)

print('tokens number: ',tokens_number)
pricing_1k_tokens_babbage = 0.0050
estimated_price = tokens_number * pricing_1k_tokens_babbage / 1000
print('estimated price: $',estimated_price)
# $ 0.0050/1K

del total_reqs, reqs_with_more_than_2000_tokens, tokens_number

numero de tokens:  380000
preço estimado: $ 1.9


In [ ]:
import pandas as pd
df = pd.read_csv('df_Req_Final.csv')

print(df.head())
print(df.shape)

In [ ]:
df['n_tokens'] = df['Cleaned'].apply(lambda x: len(tokenizer.encode(x))) # mesure number of tokens for each requirement

In [ ]:
i=-1
j=0
def truncate_tokens(requirement):
  """Returns truncated requirement tokens."""
  global i,j
  i+=1
  tokens = tokenizer.encode(requirement)
  
  if len(tokens)>=2000:
    j+=1
    return tokenizer.decode(tokens[:2000])
  return requirement

df['Truncated']=df['Cleaned'].apply(lambda x: truncate_tokens(x))
print(f'{j} truncated requirements.')
df['n_tokens_truncated']=df['Truncated'].apply(lambda x: len(tokenizer.encode(x)))


In [ ]:
import time
import openai
# from openai.embeddings_utils import get_embedding

# openai.api_key = '?'

times = []
def get_embedding(text, model="text-similarity-babbage-001"):
  start = time.time()

  text = text.replace("\n", " ")
  embedding = openai.Embedding.create(input = [text], model=model)['data'][0]['embedding']

  if((len(times)%100)==0):
    print(len(times))
  elapsed = time.time() - start
  times.append(elapsed)
  if(elapsed < 0.02):
    time.sleep(0.02-elapsed)
  return embedding
i=-1
j=0
def get_embeddings_for_tokens_bigger_than_2000(text):
  global i,j
  i+=1
  if df.iloc[i]['n_tokens']>=2000: # only generate embeddings for tokens bigger than 2000
    j+=1
    return get_embedding(text,model='text-similarity-babbage-001')
  return df.iloc[i]['babbage_similarity']
df['all_embeddings'] = df['Truncated'].apply(lambda requirement: get_embeddings_for_tokens_bigger_than_2000(requirement))
print('total requests:',j)

# Saves the results
# df.to_pickle('df_All_Embeddings.pkl')

In [ ]:
# prints generated embeddings
for i in range(23313):
  requirement = df.iloc[i]
  if requirement['n_tokens']>=2000:
    print(requirement['all_embeddings'])

[-0.012605485506355762, 0.009739803150296211, -0.005784106906503439, -0.021483825519680977, 0.014178973622620106, -0.013317510485649109, -0.026881152763962746, 0.0070411390624940395, -0.0035447434056550264, -0.02874472551047802, 0.014381153509020805, 0.000687851628754288, 0.026213079690933228, 0.021642053499817848, -0.004113924223929644, 0.02318917028605938, 0.027601968497037888, 0.006482946686446667, 0.019233474507927895, 0.024384669959545135, 0.10541491210460663, -0.0002626142813824117, 0.010759493336081505, 0.0012196729658171535, 0.018266525119543076, 0.020200422033667564, -0.01374824158847332, 0.023540787398815155, -0.035056259483098984, 0.01249120943248272, -0.004966596141457558, 0.024472573772072792, -0.009194795973598957, -0.0028502987697720528, -0.019637834280729294, -0.0358298160135746, 0.05024613067507744, -0.0038150493055582047, -0.009915611706674099, -0.005168776493519545, -0.040189873427152634, -0.0023162798024713993, 0.04592123627662659, 0.0035974858328700066, -0.02512306

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



[-0.002820469904690981, 0.03222601115703583, -0.0027186647057533264, -0.030560104176402092, 0.010199042037129402, 0.014132428914308548, -0.0172328632324934, 0.004567356780171394, 0.015937158837914467, -0.028801649808883667, 0.022526739165186882, 0.005247601307928562, 0.000618351623415947, 0.010115746408700943, 0.01525228749960661, 0.019916821271181107, 0.0290052592754364, -0.010439672507345676, 0.003463694592937827, 0.03657587245106697, 0.08329525589942932, -0.009264283813536167, -0.013660422526299953, -0.01919492892920971, -0.011291135102510452, -0.012734919786453247, -0.0422399528324604, 0.024118604138493538, -0.010078726336359978, 0.005094893276691437, -0.0012852920917794108, 0.007936187088489532, 0.011652081273496151, 0.013938073068857193, -0.015085697174072266, -0.018917279317975044, 0.06178657338023186, -0.00810740515589714, -0.009504914283752441, -0.0024919165298342705, -0.028672078624367714, 0.005650194827467203, 0.0553450733423233, -0.027968697249889374, -0.04483135789632797, 

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



[0.006829594727605581, 0.038616836071014404, 0.008207455277442932, -0.012584458105266094, 0.021219050511717796, 0.011877156794071198, -0.019933046773076057, 0.025573089718818665, 0.014100104570388794, -0.025720061734318733, 0.006567801348865032, 0.0034446511417627335, 0.0031300396658480167, 0.009332708083093166, 0.009401600807905197, 0.015340179204940796, 0.027097921818494797, -0.0133652463555336, 0.008905570954084396, 0.045891936868429184, 0.10581967979669571, -0.0023262877948582172, -0.0030106250196695328, -0.009167364798486233, -0.0054655130952596664, 0.0036421443801373243, -0.030698729678988457, 0.02391965687274933, -0.004641093313694, 0.011160669848322868, 0.015496336854994297, 0.01903284527361393, 0.006825001910328865, 0.009819552302360535, -0.0007968625868670642, -0.009681765921413898, 0.04714119806885719, -0.012823287397623062, -0.005764049477875233, -0.01821531541645527, -0.009236257523298264, 0.0059661357663571835, 0.032058220356702805, -0.01589132286608219, -0.04960297420620

In [ ]:
df.head()

Unnamed: 0                                               Text  Estimate  \
0       23009  add ca against object literals in function inv...         1   
1       23013  update branding for appcelerator plugin to app...         1   
2       23003  create new json schema for sdk team{html}<div>...         1   
3       23012  create project references property page{html}<...         1   
4       23007  new desktop project wizard{html}<div><p>deskto...         1   

                                             Cleaned  aux_id  n_tokens  \
0  add ca against object literals in function inv...       0        60   
1  update branding for appcelerator plugin to app...       1        25   
2  create new json schema for sdk team create jso...       2        68   
3  create project references property page create...       3        57   
4  new desktop project wizard desktop need to con...       4        84   

                                  babbage_similarity  \
0  [0.002614866243675351, 0.021624723449349403, -...   
1  [-0.004593433812260628, 0.012765610590577126, ...   
2  [-0.007252641953527927, 0.01757843792438507, 0...   
3  [0.004085508640855551, 0.02281530760228634, -0...   
4  [-0.029573751613497734, 0.024609791114926338, ...   

                                           Truncated  n_tokens_truncated  \
0  add ca against object literals in function inv...                  60   
1  update branding for appcelerator plugin to app...                  25   
2  create new json schema for sdk team create jso...                  68   
3  create project references property page create...                  57   
4  new desktop project wizard desktop need to con...                  84   

                                      all_embeddings  
0  [0.002614866243675351, 0.021624723449349403, -...  
1  [-0.004593433812260628, 0.012765610590577126, ...  
2  [-0.007252641953527927, 0.01757843792438507, 0...  
3  [0.004085508640855551, 0.02281530760228634, -0...  
4  [-0.029573751613497734, 0.024609791114926338, ...